<table align="left"><tr><td>
<a href="https://colab.research.google.com/github/rickiepark/nlp-with-transformers/blob/main/03_transformer-anatomy.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="코랩에서 실행하기"/></a>
</td></tr></table>

In [1]:
# Colab 이나 Kaggle 을 사용하는 경우, 이 cell의 주석을 없애고 실행하시오.
# !git clone https://github.com/rickiepark/nlp-with-transformers.git
# %cd nlp-with-transformers
# from install import *
# install_requirements(chapter=3)

저자의 원래 환경에서의 `setup_chapter()` 출력:
```

Using transformers v4.11.3
Using datasets v1.13.0
Using accelerate v0.5.1
```

In [1]:
#hide
from utils import *
setup_chapter()

Using transformers v4.11.3
Using datasets v1.16.1


# Transformer Anatomy

당면 문제를 해결하기 위해 🤗 Transformers를 사용하고 모델을 미세조정하는 데 트랜스포머 아키텍처의 기술적인 측면을 반드시 깊이 알아야 하는 것은 아니다. 그러나, 기술적인 측면을 알면 트랜스포머의 한계점을 파악하거나 새로운 도메인에 적용할 때 도움이 된다.

## The Transformer Architecture

<img src="images/chapter03_transformer-encoder-decoder.png" id="transformer-encoder-decoder" width="500" style="margin-left: auto; margin-right: auto">
<p style="text-align: center;">Figure 3-1. 트랜스포머 인코더-디코더 아키텍처. 상단이 인코더, 하단이 디코더</p>

### 트랜스포머 모델의 유형
#### Encoder-only
- 입력 시퀀스를 rich numerical representation으로 변환
- 텍스트 분류, NER
- BERT 및 BERT 변종(RoBERTa, DistilBERT, ...)
- 양방향 attention
#### Decoder-only
- 다음 단어를 예측하면서 시퀀스 완성(생성)
- GPT 계열
- autoregressive(or causal) attention
#### Encoder-decoder
- 입력 시퀀스를 출력 시퀀스로 매핑
- MT, Summarization
- 트랜스포머, BART, T5

## The Encoder

<img src="images/chapter03_encoder-zoom.png" id="encoder-zoom" width="500" style="margin-left: auto; margin-right: auto">
<p style="text-align: center;">Figure 3-2. 인코더 층을 확대한 그림</p>

- Positional embedding
- Multi-head self-attention layer
- Fully connected feed-forward layer
- Skip connection
- Layer normalization

### Self-Attention

<img src="images/chapter03_contextualized-embedding.png" id="contextualized-embeddings" width="500" style="margin-left: auto; margin-right: auto">
<p style="text-align: center;">Figure 3-3. Self-attention이 원시 token embedding을 contextualized embedding(위)으로 업데이트해서 전체 스퀀스 정보를 통합하는 표상(representation)을 만드는 방법</p>

#hide
#### 트랜스포머 모델을 위한 시각화 라이브러리 [BertViz](https://github.com/jessevig/bertviz) 사용
- BERT, GPT2, T5 같은 트랜스포머 기반 모델의 Attention 시각화를 위한 라이브러리
- Jupyter notebook 또는 JupyterLab에서 `bertviz`를 사용하기 위해 다음 magic commend를 copy해서 새 cell에서 실행시킨다.

```python
%%javascript
require.config({
  paths: {
      d3: '//cdnjs.cloudflare.com/ajax/libs/d3/3.4.8/d3.min',
      jquery: '//ajax.googleapis.com/ajax/libs/jquery/2.0.0/jquery.min',
  }
});
```

In [2]:
%%javascript
require.config({
  paths: {
      d3: '//cdnjs.cloudflare.com/ajax/libs/d3/3.4.8/d3.min',
      jquery: '//ajax.googleapis.com/ajax/libs/jquery/2.0.0/jquery.min',
  }
});

<IPython.core.display.Javascript object>

In [3]:
#hide_output
from transformers import AutoTokenizer
from bertviz.transformers_neuron_view import BertModel
from bertviz.neuron_view import show

model_ckpt = "bert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)
model = BertModel.from_pretrained(model_ckpt)
text = "time flies like an arrow"
show(model, "bert", tokenizer, text, display_mode="light", layer=0, head=8)

Downloading:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/570 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/226k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/455k [00:00<?, ?B/s]

100%|████████████████████████████████████████████████████████████████████████| 440473133/440473133 [04:15<00:00, 1723480.15B/s]


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

#### Scaled dot-product attention

<img src="images/chapter03_attention-ops.png" id="attention-ops" width="500" style="margin-left: auto; margin-right: auto">
<p style="text-align: center;">Figure 3-4. Scaled dot-product attention</p>

텍스트 토큰화

In [4]:
# hide
from transformers import AutoTokenizer
model_ckpt = "bert-base-uncased"
text = "time flies like an arrow"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)

In [5]:
inputs = tokenizer(text, return_tensors="pt", add_special_tokens=False) 
inputs.input_ids

tensor([[ 2051, 10029,  2066,  2019,  8612]])

- `return_tensors="pt"` : 출력을 PyTorch tensor로 받는다
- `add_special_tokens=False` : [CLS] 나 [SEP] 같은 특수 토큰을 지정하지 않음

Dense embedding 생성
- `torch.nn.Embedding`은 각 입력 ID에 대해 lookup table 같은 역할을 함
- `AutoConfig` : bert-base-uncased checkpoint와 관련된 _config.json_ 파일을 읽어들임
- 🤗 Transformers에서는 모든 checkpoint 마다 configuration file이 생긴다.
- _config.json_ : `vocab_size`나 `hidden_size` 같은 hyperparameter들과 레이블명 같은 metadata가 저장됨

In [6]:
from torch import nn
from transformers import AutoConfig

config = AutoConfig.from_pretrained(model_ckpt)
token_emb = nn.Embedding(config.vocab_size, config.hidden_size)
token_emb

Embedding(30522, 768)

- 이 단계에서 token embedding은 context와 독립적이다.
- 즉, homonym(동철이의어) 같은 중의성 문제가 그대로 있다('깡통' can과 '조동사' can 의 embedding vector가 동일함)
- 이후 Attention layer들을 거치면서 중의성(모호함)이 해결된다

In [7]:
inputs_embeds = token_emb(inputs.input_ids)
inputs_embeds.size()

torch.Size([1, 5, 768])

- 출력 torch.Size([1, 5, 768]) ⟹ `[batch_size, seq_len, hidden_dim]`

<span style="color:red">**[주의]** </span> 원래는 순서는 Positional encoding 이나, 여기서는 잠시 뒤로 미룬다. 

query, key, 및 value 벡터를 생성하고 유사도 함수로 dot product(내적)을 사용하여 attention scores를 계산한다.

In [8]:
import torch
from math import sqrt 

query = key = value = inputs_embeds
dim_k = key.size(-1)
scores = torch.bmm(query, key.transpose(1,2)) / sqrt(dim_k)
scores.size()

torch.Size([1, 5, 5])

- Batch 내 한 샘플 당 한개의 (5 x 5) attention score matrix를 생성.
- query, key, value 벡터는 임베딩 벡터에 $W_Q$, $W_K$, $W_V$ 를 적용해서 구하지만 여기서는 설명을 단순화하기 위해 생략했다.

<span style="color:red">**[노트]** </span> **`torch.bmm()` 함수** <br>
- batch matrix-matrix 곱셈 수행
- 이 예에서는 각 행렬의 차원이 `[batch_size, seq_len, hidden_dim]`이므로, 결과는 `[batch_size, seq_len, seq_len]`

softmax 적용

In [9]:
import torch.nn.functional as F

weights = F.softmax(scores, dim=-1)
weights.sum(dim=-1)

tensor([[1., 1., 1., 1., 1.]], grad_fn=<SumBackward1>)

Attention weught 와 value 의 곱

In [10]:
attn_outputs = torch.bmm(weights, value)
attn_outputs.shape

torch.Size([1, 5, 768])

정리하여 Scaled dot-product attention을 계산하는 함수로 만들어 두자.

In [11]:
def scaled_dot_product_attention(query, key, value):
    dim_k = query.size(-1)
    scores = torch.bmm(query, key.transpose(1, 2)) / sqrt(dim_k)
    weights = F.softmax(scores, dim=-1)
    return torch.bmm(weights, value)

- 동일한 query와 key 벡터를 사용하는 attention mechanism은 context에서 동일한 단어, 특히 현재 읽어들인 단어에 매우 큰 점수를 할당한다.
- 그러나, 실제 단어의 의미를 파악하는 데 도움이 되는 것은 문맥을 보완하는 단어들이다.
- 예: 'flies'의 의미는 'time'과 'arrow'의 정보를 통합할 때 더 잘 정의된다.
- 어떤 원리로 이렇게 되는 것일까?

#### Multi-headed attention

- 지금까지의 단순 예시에서는 임베딩 벡터를 변환 없이 그대로 사용하여 attention score를 구했으나(query, key, value 벡터가 모두 같았음)
- 그러나, 실제 트랜스포머 모델에서는 3가지의 다른 선형변환을 통해 서로 다른 query, key, value를 만들어 이것으로 attention score를 계산한다(self-attention이 시퀀스의 다른 의미적 측면에 집중할 수 있게 해준다).
- 선형변환을 여러 벌 갖는 것이 유익하다는 것이 알려져 있다(CNN의 한 층에 여러가지 필터를 사용하는 것과 유사).
- 각 선형변환을 attention-head 라고하면, 우리는 multihead attention 층을 갖는 셈이다.

<img src="images/chapter03_multihead-attention.png" id="multihead-attention" width="500" style="margin-left: auto; margin-right: auto">
<p style="text-align: center;">Figure 3-5. Multihead-Attention</p>

**Multihead-Attention이 필요한가?**  
- 한 head의 softmax는 유사도의 한 측면에만 촛점을 맞추는 경향이 있기 때문이다.

In [12]:
class AttentionHead(nn.Module):
    def __init__(self, embed_dim, head_dim):
        super().__init__()
        # q, k, v 를 만들기 위한 linear layer들
        # 입력: [batch_size, seq_len, embed_dim]
        # 출력: [batch_size, seq_len, head_dim]
        self.q = nn.Linear(embed_dim, head_dim) 
        self.k = nn.Linear(embed_dim, head_dim) 
        self.v = nn.Linear(embed_dim, head_dim)

    def forward(self, hidden_state):
        attn_outputs = scaled_dot_product_attention(
            self.q(hidden_state), self.k(hidden_state), self.v(hidden_state))
        return attn_outputs

- head_dim은 head_dim = embed_dim/num_head 로 설정하는 것이 일반적.
- BERT 의 경우, head_dim = embed_dim/num_head = 768/12 = 64

In [13]:
class MultiHeadAttention(nn.Module):
    def __init__(self, config):
        super().__init__()
        embed_dim = config.hidden_size
        num_heads = config.num_attention_heads
        head_dim = embed_dim // num_heads
        self.heads = nn.ModuleList(
            [AttentionHead(embed_dim, head_dim) for _ in range(num_heads)]
        )
        self.output_linear = nn.Linear(embed_dim, embed_dim) # [batch_size, seq_len, hidden_dim]

    def forward(self, hidden_state):
        x = torch.cat([h(hidden_state) for h in self.heads], dim=-1)
        x = self.output_linear(x)
        return x

`self.heads`에 저장된 각 attention head의 출력을 concatenate해야 embed_dim 크기의 벡터가 됨에 주목

In [14]:
multihead_attn = MultiHeadAttention(config)
attn_output = multihead_attn(inputs_embeds)    
attn_output.size() 

torch.Size([1, 5, 768])

In [16]:
#hide_output
from bertviz import head_view
from transformers import AutoModel

model = AutoModel.from_pretrained(model_ckpt, output_attentions=True)

sentence_a = "time flies like an arrow"
sentence_b = "fruit flies like a banana"

viz_inputs = tokenizer(sentence_a, sentence_b, return_tensors='pt')
attention = model(**viz_inputs).attentions
sentence_b_start = (viz_inputs.token_type_ids == 0).sum(dim=1)
tokens = tokenizer.convert_ids_to_tokens(viz_inputs.input_ids[0])

head_view(attention, tokens, sentence_b_start, heads=[8])

<IPython.core.display.Javascript object>

- 같은 문장에 속한 토큰 사이의 attention weight들이 가장 강하다. 
- 첫째문장 'flies'(동사) -- 'arrow', 둘째문장 'files'(명사) -- 'fruit' & 'banana'
- Attention weight는 'files'가 문맥에 따라 동사 또는 명사로 사용되는 것을 구분할 수 있게 해준다

### The Feed-Forward Layer

- Embedding 벡터 시퀀스 전체를 한꺼번에 처리하지 않고 각 embedding vector를 독립적으로 처리
  - 때문에 _position-wise feed-forward layer_라고 부르기도 함
  - 컴퓨터 비젼 전문가에게는 kernel size가 1인 1차원 convolution으로 보일 수도 있음(OpenAI GPT에서는 이렇게 칭함)
- 첫번째 layer에서, 은닉층 크기 `intermediate_size`는 보통 4 x embed_dim
- GELU : Gaussian Error Linear Unit 활성화 함수
- <span style="color:IndianRed">대부분의 용량(model capacity)과 기억(memorization)이 발생한다고 가정되는 부분이며, 모델을 확장할 때 가장 자주 확장되는 부분이다.</span>


In [17]:
class FeedForward(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.linear_1 = nn.Linear(config.hidden_size, config.intermediate_size)
        self.linear_2 = nn.Linear(config.intermediate_size, config.hidden_size)
        self.gelu = nn.GELU()
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        
    def forward(self, x):
        x = self.linear_1(x)
        x = self.gelu(x)
        x = self.linear_2(x)
        x = self.dropout(x)
        return x

- `nn.Linear`에 크기 [batch_size, seq_len, hidden_dim]인 텐서를 통과시키면 layer가 모든 batch 및 sequence의 각 token embedding에 독립적으로 적용된다.

In [18]:
feed_forward = FeedForward(config)
ff_outputs = feed_forward(attn_outputs)
ff_outputs.size()

torch.Size([1, 5, 768])

이제 Layer Normalization과 Skip Connection을 추가할 차례다.

### Adding Layer Normalization

- Layer Normalization : Batch에 있는 각 입력을 평균이 0이고 분산이 1이 되도록 정규화
- Skip Connection : 처리하지 않은 텐서를 다음 층으로 직접 전달하고 처리된 텐서와 더하는 것

##### Post layer normalization
- 트랜스포머 논문에서 사용하는 방법
- skip connection 사이에 위치
- Gradient가 발산하기 쉬워 처음부터 훈련하기 까다로움
- 때문에, _learning rate warm-up_ 방법을 사용하기도 함
##### Pre layer normalization
- 다수의 논문에 제시된 방법
- skip connection 내부에 위치
- 훨씬 안정적으로 훈련되는 경향이 있으며 learning rate warm-up이 필요 없음

<img src="images/chapter03_layer-norm.png" id="layer-norm" width="500" style="margin-left: auto; margin-right: auto">
<p style="text-align: center;">Figure 3-6. 트랜스포머 인코더 층의 layer mormalization 배치 방법</p>

두 번째 방법(Pre layer normalization)으로 구현한다.

In [19]:
class TransformerEncoderLayer(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.layer_norm_1 = nn.LayerNorm(config.hidden_size)
        self.layer_norm_2 = nn.LayerNorm(config.hidden_size)
        self.attention = MultiHeadAttention(config)
        self.feed_forward = FeedForward(config)

    def forward(self, x):
        # layer normalization 하고 입력을 query, key, value 로 copy
        hidden_state = self.layer_norm_1(x)
        # Apply attention with a skip connection
        x = x + self.attention(hidden_state)
        # Apply feed-forward layer with a skip connection
        x = x + self.feed_forward(self.layer_norm_2(x))
        return x

In [20]:
encoder_layer = TransformerEncoderLayer(config)
inputs_embeds.shape, encoder_layer(inputs_embeds).size()

(torch.Size([1, 5, 768]), torch.Size([1, 5, 768]))

인코더 층을 처음부터 구현했다! 그러나 주의할 점이 있다.
- 이 인코더 층은 토큰의 시퀀스 내 위치를 고려하지 않는다.
- Multihea-attention 층은 사실 멋진 가중합(weighted sum)이므로 토큰 위치에 대한 정보가 사라지게 된다.
  (self-attention 층과 feed-forward 층은 _permutation equivariant_ 하다)

### Positional Embeddings

**Idea** : 벡터 내에 나열된 값들의 위치의존적 패턴으로 토큰 임베딩을 보강한다.
- 만일 패턴에 각 위치에 대한 특성이 담겼다면, 각 스택의 attention head들과 feed-forward layer들이 변환과정에 위치 정보를 통합하는 방법을 학습하게 될 것이다. 
- 위치 임베딩에는 여러 방법이 있으나, 트랜스포머는 학습가능 패턴을 사용한다.
- 이 방법은 대량의 데이터가 있는 경우 특히 효과적이다.
- 트랜스포머는 사전학습 동안에 토큰의 위치를 인코딩하는 효율적인 방법을 학습하게 된다.

In [21]:
class Embeddings(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.token_embeddings = nn.Embedding(config.vocab_size, 
                                             config.hidden_size)
        self.position_embeddings = nn.Embedding(config.max_position_embeddings,
                                                config.hidden_size)
        self.layer_norm = nn.LayerNorm(config.hidden_size, eps=1e-12)
        self.dropout = nn.Dropout()

    def forward(self, input_ids):
        # 입력 시퀀스에 대해 위치 ID를 만든다
        seq_length = input_ids.size(1)
        position_ids = torch.arange(seq_length, dtype=torch.long).unsqueeze(0)
        # 토큰 임베딩과 위치 임베딩을 만든다
        token_embeddings = self.token_embeddings(input_ids)
        position_embeddings = self.position_embeddings(position_ids)
        # 토큰 임베딩과 위치 임베딩을 합친다
        embeddings = token_embeddings + position_embeddings
        embeddings = self.layer_norm(embeddings)
        embeddings = self.dropout(embeddings)
        return embeddings

In [22]:
embedding_layer = Embeddings(config)
embedding_layer(inputs.input_ids).size()

torch.Size([1, 5, 768])

#### Positional Embedding 방법들
##### Absolute positional representations
- 변조된 sine 및 cosine 신호로 구성된 static pattern을 사용
- 트랜스포머 포함, 가용 데이터가 많지 않은 경우 유리
##### Relative positional representations
- 절대 위치보다 대상 토큰의 주변 토큰들이 더 중요하다고 보는 방법
- 상대 위치 임베딩 층을 추가하는 방식으로 구현할 수 없음
- Attention mechanism 자체에 상대 위치를 고려하는 부분을 추가하는 방식으로 구현(예: DeBERTa)
##### Rotary positional representations
- 위의 두가지 개념을 합친 개념
- 좋은 성능을 보임(예: GPT-Neo)

In [23]:
class TransformerEncoder(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.embeddings = Embeddings(config)
        self.layers = nn.ModuleList([TransformerEncoderLayer(config) 
                                     for _ in range(config.num_hidden_layers)])

    def forward(self, x):
        x = self.embeddings(x)
        for layer in self.layers:
            x = layer(x)
        return x

In [24]:
encoder = TransformerEncoder(config)
encoder(inputs.input_ids).size()

torch.Size([1, 5, 768])

- 트랜스포머 인코더의 출력(hidden state) 형식은 이어지는 태스크들에서 이용하기 매우 편리하다.

### Adding a Classification Head

지금까지 트랜스포머 모델의 Body를 만든 것이다. 특정 태스크를 위해 Head 부분을 더해본다. 
- 분류 Head의 경우, 첫번째 토큰(`[CLS]`)을 예측에 사용하고 Drop-out과 Linear 층을 추가해 분류 예측을 만든다.

In [25]:
class TransformerForSequenceClassification(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.encoder = TransformerEncoder(config)
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        self.classifier = nn.Linear(config.hidden_size, config.num_labels)
        
    def forward(self, x):
        x = self.encoder(x)[:, 0, :] # [CLS] 토큰의 은닉 상태를 선택
        x = self.dropout(x)
        x = self.classifier(x)
        return x

In [26]:
config.num_labels = 3
encoder_classifier = TransformerForSequenceClassification(config)
encoder_classifier(inputs.input_ids).size()

torch.Size([1, 3])

In [27]:
inputs.input_ids

tensor([[ 2051, 10029,  2066,  2019,  8612]])

In [28]:
encoder_classifier(inputs.input_ids)

tensor([[ 0.7317, -0.3283, -1.8290]], grad_fn=<AddmmBackward0>)

- Batch에 있는 각 샘플에 대해, 출력의 각 클래스에 대한 비정규화된 로짓(logit)을 얻는다.
- 2장의 트윗 감정 분류를 위한 BERT 모델과 같다.

## The Decoder

<img src="images/chapter03_decoder-zoom.png" id="decoder-zoom" width="500" style="margin-left: auto; margin-right: auto">
<p style="text-align: center;">Figure 3-7. 트랜스포머 인코더 층을 확대한 그림</p>

#### Decoder가 Encoder와 다른 점
##### Masked multi-head self-attention layer
- 각 timestep에서, 과거 출력과 현재 예측 중인 토큰만을 기반으로 토큰을 예측하도록 한다.
- 이 기능이 없으면 훈련 중에 Decoder가 단순히 대상 번역을 복사하는 식으로 속임수를 쓸 수 있다.
##### Encoder-decoder attention layer
- Decoder의 중간 표현(표상)이 query 로 사용하여 Encoder 스택의 출력 key와 value 벡터에 대해 multi-head attention을 수행
- Encoder-Decoder의 attention layer는 서로 다른 두 언어와 같이 서로 다른 두 시퀀스의 토큰을 연관시키는 방법을 학습하게 됨.
- Decoder는 각 블록의 Encoder key와 value에 액세스할 수 있다.

Self-attention 층에 masking을 포함시키기 위한 방안

In [29]:
seq_len = inputs.input_ids.size(-1)
mask = torch.tril(torch.ones(seq_len, seq_len)).unsqueeze(0)
mask[0]

tensor([[1., 0., 0., 0., 0.],
        [1., 1., 0., 0., 0.],
        [1., 1., 1., 0., 0.],
        [1., 1., 1., 1., 0.],
        [1., 1., 1., 1., 1.]])

Mask의 0을 $-\infty$로 바꾸어, attention head가 미래 토큰들을 훔쳐볼 수 없게 만든다.

In [30]:
scores.masked_fill(mask == 0, -float("inf"))

tensor([[[ 2.7334e+01,        -inf,        -inf,        -inf,        -inf],
         [-2.9541e-01,  2.8700e+01,        -inf,        -inf,        -inf],
         [ 1.1974e+00, -4.7377e-01,  2.8327e+01,        -inf,        -inf],
         [ 3.1336e-03,  7.6578e-02,  1.0298e-01,  2.7906e+01,        -inf],
         [-6.7991e-01,  1.0864e+00, -2.1391e-01,  9.9259e-02,  2.7846e+01]]],
       grad_fn=<MaskedFillBackward0>)

scaled_dot_product_attention 함수에 masking 기능 추가하기

In [31]:
def scaled_dot_product_attention(query, key, value, mask=None):
    dim_k = query.size(-1)
    scores = torch.bmm(query, key.transpose(1, 2)) / sqrt(dim_k)
    if mask is not None:
        scores = scores.masked_fill(mask == 0, float("-inf"))
    weights = F.softmax(scores, dim=-1)
    return weights.bmm(value)

### <span style="color:red">[Homework] Encoder-Decoder Attention Layer 구현</span>
- 마감 일자 및 세부 내용은 이클래스 과제 공고 참조할 것. 

Decoder 층 구현을 위한 참조 사이트: Andrej Karpathy의 [minGPT](https://github.com/karpathy/minGPT).

### Sidebar: Demystifying Encoder-Decoder Attention

### End sidebar

## Meet the Transformers

### <span style="color: IndianRed">이하는 강의 슬라이드를 볼 것</span>

### The Transformer Tree of Life

<img src="images/chapter03_transformers-compact.png" id="family-tree" width="500" style="margin-left: auto; margin-right: auto">
<p style="text-align: center;">Figure 3-8. 대표적인 트랜스포머 아키텍처 가계도</p>

### The Encoder Branch

### The Decoder Branch

### The Encoder-Decoder Branch

## Conclusion